In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
from DBSCANSupport import DBSCANSupport
from LocalPath import LOCALPATH
from sklearn.cluster import DBSCAN

In [2]:
grav = pd.read_csv(LOCALPATH + 'data/test_grav.csv').drop(columns=["old_ind"])
grav = grav[['Longitude', 'Latitude', 'Intensity']]

In [3]:
Z = DBSCANSupport.formatData(grav, 'Intensity')
#Z = Z[(Z[:, 2] > -20) & (Z[:, 2] < 7)]
data = Z

/Users/seamount_picking_stable/seamount_picking/code/_SeamountSupport.py:264: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["TrueSeamount"] = np.zeros(data.shape[0])


In [4]:
## Elbow test
from sklearn.neighbors import NearestNeighbors
from matplotlib import pyplot as plt
neighbors = NearestNeighbors(n_neighbors=20)
neighbors_fit = neighbors.fit(data)
distances, indices = neighbors_fit.kneighbors(data)
distances = np.sort(distances, axis=0)
distances = distances[:,1]
elbow = px.scatter(x=range(0, len(distances)), y=distances)#.show()

In [5]:
test_eps = np.linspace(0.1, 0.5, 20)
test_samp = np.arange(2, 10)
DBModel_test = DBSCANSupport(LOCALPATH+"data/sample_mask.txt.xlsx", train_zone=(-6, -1, -98, -90))
DBModel_test.addTrainingData(data)

In [6]:
score, params, data_out, out  = DBModel_test.gridSearch(test_eps, test_samp, verbose=True)

Score for 0.1 and 2 is -71.92031334070506 with 198 clusters
Score for 0.1 and 3 is -71.92031334070506 with 145 clusters
Score for 0.1 and 4 is -70.67257200909326 with 122 clusters
Score for 0.1 and 5 is -59.33349782486202 with 113 clusters
Score for 0.1 and 6 is -44.876177915298896 with 96 clusters
Score for 0.1 and 7 is -39.63179945747357 with 86 clusters
Score for 0.1 and 8 is -33.15616195765918 with 71 clusters
Score for 0.1 and 9 is -30.458647957988372 with 59 clusters
Score for 0.12105263157894737 and 2 is -132.74872050541012 with 120 clusters
Score for 0.12105263157894737 and 3 is -132.74872050541012 with 85 clusters
Score for 0.12105263157894737 and 4 is -117.48622485941974 with 78 clusters
Score for 0.12105263157894737 and 5 is -108.159629634337 with 66 clusters
Score for 0.12105263157894737 and 6 is -80.40689707421245 with 56 clusters
Score for 0.12105263157894737 and 7 is -67.12600900233967 with 49 clusters
Score for 0.12105263157894737 and 8 is -56.814299417746646 with 50 cl

In [7]:
dfout = pd.DataFrame(data_out, columns=["Lat", "Lon", "Label", "Intensity", "TrueLabel"])
df_labeled = dfout[dfout['Label'] != 0]

In [8]:
test_zone=(-6, -1.5, -98, -90)
seamounts = pd.read_excel(LOCALPATH+"data/sample_mask.txt.xlsx", \
                              sheet_name="new mask")
seamounts = seamounts.drop(columns=["VGG Height", "Radius", "base_depth", "-",
                                        "Name", "Charted", "surface_depth"])
seamounts = seamounts[(seamounts["Latitude"] >= test_zone[0]) & (seamounts["Latitude"] <= test_zone[1]) &
                          (seamounts["Longitude"] >= test_zone[2]) & (seamounts["Longitude"] <= test_zone[3])]
seamounts = seamounts.to_numpy()

In [25]:
fig = px.scatter(df_labeled, x="Lon", y="Lat", color="TrueLabel", width=1300, height=800)
fig.add_trace(px.scatter(x=seamounts[:, 0], y=seamounts[:, 1]).data[0])
fig.update_xaxes(
    scaleanchor="y",
    scaleratio=1,
  )
fig.show()

In [26]:
fig2 = px.scatter(dfout, x="Lon", y="Lat", color="TrueLabel", width=1300, height=800)
fig2.update_xaxes(
    scaleanchor="y",
    scaleratio=1,
  )

In [15]:
with open(LOCALPATH + "out/best.txt", "r") as f:
    lines = f.read()
    lines = lines.split("\n")
    scores = [line for line in lines if "Score" in line]
    scores = [float(score.split(": ")[-1]) for score in scores]
    best = np.argmax(scores)


In [16]:
with open(LOCALPATH + "out/best.txt", "a") as f:
    f.write("Score: " + str(score) + "\n")
    f.write("Params: " + str(params) + "\n")
    f.write("Used Outliers: " + str(out) + "\n")
if score > best:
    DBModel_test.matchPoints().to_csv(LOCALPATH + "out/matched.csv", index=False)
    dfout.to_csv(LOCALPATH + "out/labels.csv", index=False)
